# Loading data

In [30]:
from IPython import get_ipython
get_ipython().magic('reset -sf') 

/var/folders/3d/rj_5kf356tlcqkyldb_hym1h0000gn/T/ipykernel_4921/3019614859.py:2: DeprecationWarning: `magic(...)` is deprecated since IPython 0.13 (warning added in 8.1), use run_line_magic(magic_name, parameter_s).
  get_ipython().magic('reset -sf')


In [32]:
# Preliminary
import pandas as pd
import os

my_dir = '/Users/jindi/Documents/GitHub/pp4r_final_assignments' # change this to your path

os.chdir(my_dir) 

In [33]:
# Read file
df = pd.read_csv('data/Homegate_data_cleaned.csv')

# Packages and steps in cmd 

In [38]:
# first we need to install folium:
    # in cmd: pip install folium

import folium as fl
print(fl.__version__)

import json
import matplotlib as mpl

0.14.0


In [ ]:
# we need the boundaries of the map, we can download it from
    # https://www.swisstopo.admin.ch/en/geodata/official-geographic-directories/directory-towns-cities.html#download

# we shouldn't forget to reference this correctly later :)

In [8]:
# install GDAL – Geospatial Data Abstraction Library
    # conda install -c conda-forge gdal
# and geopandas
    # conda install geopandas

## Maps for Zurich

### Postal codes from mikpan

In [39]:
# getting postcode boundaries from other source:
# https://github.com/mikpan/ch-maps/blob/master/geo/ch-plz.geojson

zh_2 = fl.Map(location=[47.3769, 8.5417], zoom_start=12, tiles="Stamen Terrain")

with open('data/ch-plz.geojson', 'r') as geojson_file:
    zurich_postcodes_geojson_2 = json.load(geojson_file)

fl.GeoJson(zurich_postcodes_geojson_2).add_to(zh_2)

In [40]:
zh_2

In [7]:
zurich_postcodes_geojson_2
zurich_postcodes_geojson_2["features"]
len(zurich_postcodes_geojson_2["features"])


# one example
zurich_postcodes_geojson_2["features"][50]["id"]

6718

### Postal codes from another Swiss website

In [41]:
# from https://www.swisstopo.admin.ch/en/geodata/official-geographic-directories/directory-towns-cities.html#download

# creating missing shx files if any:
from osgeo import gdal
import geopandas as gpd
gdal.SetConfigOption('SHAPE_RESTORE_SHX', 'YES')
in_vector = my_dir + "/data/PLZO_SHP_LV95" 
gdf = gpd.read_file(in_vector)

# with geojson
os.chdir(in_vector)



In [ ]:
# in cmd:
# conda activate
# ogr2ogr -f GeoJSON -t_srs EPSG:4326 -simplify 1000 zurich_plz.geojson PLZO_PLZ.shp
# ogr2ogr -f GeoJSON -t_srs EPSG:4326 -simplify 1000 zurich_plz_os.geojson PLZO_OS.shp
# ogr2ogr -f GeoJSON -t_srs EPSG:4326 -simplify 1000 zurich_plz_osnamepos.geojson PLZO_OSNAMEPOS.shp

## Creating the aggregated data

In [43]:
# creating aggregated data for postcodes - here average prices
aggr_df = df.groupby('Postcode')['Gross Rent (CHF)'].mean().reset_index()

aggr_df['Postcode'] = aggr_df['Postcode'].astype(int)

aggr_df




Postcode  Gross Rent (CHF)
0       8001       4459.562500
1       8002       4204.250000
2       8003       3012.509804
3       8004       3119.355932
4       8005       3098.913043
5       8006       3894.744681
6       8008       4355.200000
7       8032       3670.475000
8       8037       2648.695652
9       8038       3438.500000
10      8041       3219.500000
11      8044       4276.333333
12      8045       3360.454545
13      8046       2499.500000
14      8047       2972.000000
15      8048       2404.324324
16      8049       2871.950000
17      8050       2749.045455
18      8051       1952.360000
19      8052       2549.125000
20      8053       2697.750000
21      8055       2895.888889
22      8057       2469.958333
23      8064       2216.500000
24      8102       1716.500000
25      8103       2542.000000
26      8105       2032.400000
27      8117       1993.666667
28      8118       2318.250000
29      8121       2675.000000
30      8122       1856.666667
31      8125       2663.111111
32      8126       2000.000000
33      8134       2534.466667
34      8142       3228.333333
35      8143       2669.000000
36      8152       2234.162791
37      8153       1765.000000
38      8304       2347.090909
39      8305       2475.000000
40      8600       2173.676471
41      8702       4307.538462
42      8802       4896.062500
43      8902       1974.000000
44      8903       2495.000000
45      8907       2700.000000
46      8952       2468.416667

In [44]:
post_code_list = aggr_df["Postcode"].values

post_code_list

array([8001, 8002, 8003, 8004, 8005, 8006, 8008, 8032, 8037, 8038, 8041,
       8044, 8045, 8046, 8047, 8048, 8049, 8050, 8051, 8052, 8053, 8055,
       8057, 8064, 8102, 8103, 8105, 8117, 8118, 8121, 8122, 8125, 8126,
       8134, 8142, 8143, 8152, 8153, 8304, 8305, 8600, 8702, 8802, 8902,
       8903, 8907, 8952])

## Selecting the postcodes in Zurich canton
### Sticking to zh_2 because it seemed the most complete

In [10]:
# example
zurich_postcodes_geojson_2["features"][50]["id"]

6718

In [45]:
# selecting the relevant indeces
import numpy as np
indices = []

for i in range(len(zurich_postcodes_geojson_2["features"])):
    if zurich_postcodes_geojson_2["features"][i]["id"] in post_code_list:
        indices.append(i)

indices = np.array(indices)

print(indices)
print(len(indices))

[ 800  819  830  876 1369 1379 1413 1626 1696 1727 1768 1785 1839 1891
 1935 1972 2025 2034 2145 2180 2266 2276 2280 2359 2395 2442 2454 2484
 2538 2605 2668 2836 2850 2973 3014 3097 3101 3160 3184 3221 3224 3327
 3330 3470 3606 3613 3666 3708 3844 3918 3959 4005]
52


In [46]:
# combining them into a new geojson file

zurich_boundaries = zurich_postcodes_geojson_2.copy()

zurich_boundaries["features"] = [zurich_postcodes_geojson_2["features"][i] for i in indices]

zurich_boundaries


{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 8600,
   'properties': {},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[8.59121392916002, 47.38663621395175],
      [8.583048107618108, 47.38822875216357],
      [8.583955421122765, 47.39161289586367],
      [8.589852958903036, 47.393006366799014],
      [8.589852958903036, 47.39658957777559],
      [8.596204153435634, 47.39639051049912],
      [8.593935869673992, 47.40216346151694],
      [8.59711146694029, 47.405945739770004],
      [8.59711146694029, 47.405945739770004],
      [8.597565123692618, 47.405945739770004],
      [8.602101691215903, 47.40375599972876],
      [8.606638258739189, 47.403955067005235],
      [8.607545572243845, 47.40654294159943],
      [8.6148040802811, 47.40813547981124],
      [8.618886991052058, 47.40733921070534],
      [8.628413782850956, 47.41032521985249],
      [8.634764977383554, 47.40654294159943],
      [8.645652739439438, 47.397584914157974],
      [8.651550277219

In [47]:
zh_boundaries = fl.Map(location=[47.3769, 8.5417], zoom_start=11, tiles="Stamen Terrain")

fl.GeoJson(zurich_boundaries).add_to(zh_boundaries)

zh_boundaries
# zurich_postcodes_geojson_2["features"][50]

## Merging the two data sets

In [48]:
# merging the geojson file with our own aggr_df
for i in range(len(zurich_boundaries["features"])):
    zurich_boundaries["features"][i]["average"] = int(aggr_df.loc[aggr_df['Postcode'] == zurich_boundaries["features"][i]["id"], "Gross Rent (CHF)"].values)

zurich_boundaries
# now we have the average prices in the geojson

/var/folders/3d/rj_5kf356tlcqkyldb_hym1h0000gn/T/ipykernel_4921/3810014664.py:3: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  zurich_boundaries["features"][i]["average"] = int(aggr_df.loc[aggr_df['Postcode'] == zurich_boundaries["features"][i]["id"], "Gross Rent (CHF)"].values)


{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 8600,
   'properties': {},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[8.59121392916002, 47.38663621395175],
      [8.583048107618108, 47.38822875216357],
      [8.583955421122765, 47.39161289586367],
      [8.589852958903036, 47.393006366799014],
      [8.589852958903036, 47.39658957777559],
      [8.596204153435634, 47.39639051049912],
      [8.593935869673992, 47.40216346151694],
      [8.59711146694029, 47.405945739770004],
      [8.59711146694029, 47.405945739770004],
      [8.597565123692618, 47.405945739770004],
      [8.602101691215903, 47.40375599972876],
      [8.606638258739189, 47.403955067005235],
      [8.607545572243845, 47.40654294159943],
      [8.6148040802811, 47.40813547981124],
      [8.618886991052058, 47.40733921070534],
      [8.628413782850956, 47.41032521985249],
      [8.634764977383554, 47.40654294159943],
      [8.645652739439438, 47.397584914157974],
      [8.651550277219

In [17]:
zurich_boundaries["features"][1]

{'type': 'Feature',
 'id': 8153,
 'properties': {},
 'geometry': {'type': 'Polygon',
  'coordinates': [[[8.500482578694326, 47.44556012778888],
    [8.50229720570364, 47.44954147331841],
    [8.51137034075021, 47.45252748246556],
    [8.510009370493224, 47.45869856803634],
    [8.515906908273493, 47.4590967025893],
    [8.516814221778152, 47.4624808462894],
    [8.531784894604991, 47.4650687208836],
    [8.53813608913759, 47.46865193186018],
    [8.539950716146903, 47.465864989989505],
    [8.551292134955116, 47.46905006641313],
    [8.554467732221415, 47.46666125909541],
    [8.544940940422517, 47.454916289783284],
    [8.548570194441144, 47.45332375157147],
    [8.545848253927172, 47.44755080055364],
    [8.550384821450457, 47.44376852230059],
    [8.548116537688816, 47.443370387747635],
    [8.554467732221415, 47.43580583124152],
    [8.550838478202786, 47.43102821660607],
    [8.542672656660873, 47.434014225753224],
    [8.537228775632933, 47.431426351159026],
    [8.52543370007239

## Plotting the geojson with the averages as shades of colors

In [19]:
zh_boundaries = fl.Map(location=[47.3769, 8.5417], zoom_start=11, tiles="Stamen Terrain")

for feature in zurich_boundaries["features"]:
    # for one area:
    my_opacity = (feature["average"]-1500) / 3500
    #print(i)
    #print(my_opacity)

    geojson_layer = fl.GeoJson(feature,
            style_function = lambda x, opacity=my_opacity: {
            'fillColor': "red",
            'fillOpacity': opacity,
            'color': 'black',
            'weight': 1
        }).add_to(zh_boundaries)
    
    geojson_layer.add_to(zh_boundaries)


#fl.LayerControl().add_to(zh_boundaries)

zh_boundaries

In [29]:
# saving the files
zh_boundaries.save('map.html')
